---

# S03E06 : Fonctions & décorateurs - Module functools

Cyril Desjouy

---



## 1. Introspection

L'introspection est la capacité d'un objet de connaitre ses propres attributs. L'introspection est très puissante sous Python. Par exemple, une fonction connait entre autres son nom et sa documentation. Prenons l'exemple de la fonction built-in `len`:

```python
>> len.__name__
'len'
>> len.__doc__          # Equivalent to help(len)
Return the number of items in a container.
```

## 2. Les décorateurs

<div class="alert alert-block alert-info">
Reprenez l'exemple du notebook précédent et observez les attributs <code>__name__</code> et <code>__doc__</code> de la fonction <code>stuff</code> décorée.
</div>

In [2]:
def prettier(func):
    def wrapper(*args, **kwargs):
        result = func(*args, **kwargs)
        print('.oOO Processing OOo.'.center(80))
        print(result)
        print('.oOO ~~~Done~~~ OOo.'.center(80))
        return result                            # Return func(*args, **kwargs)
    return wrapper

@prettier
def stuff(task, like_a=''):
    return f'Doing {task} like a {like_a}'.center(80)

Vous aurez remarqué qu'après avoir été décorée, `stuff` a perdu ses attributs `__name__` et `__doc__`  qui ont été remplacés par ceux de `wrapper`. Pour corriger ce problème, les décorateurs peuvent eux même utiliser le décorateur `wraps` fournit par le module standard `functools`. Ce décorateur permet en particulier de préserver les attributs originaux de la fonction décorée:

<div class="alert alert-block alert-info">
Quels sont maintenant les valeurs des attributs <code>__name__</code> et <code>__doc__</code> de la fonction <code>stuff</code> décorée.
</div>

**Note:** *`wrap` est une fonction de confort pour invoquer `update_wrapper` en tant que décorateur. Si vous devez utiliser `wrap` sous une forme fonctionnelle, il faudra plutôt utiliser `update_wrapper`:*
```python
update_wrapper(wrapper, wrapped)   # dans notre cas: update_wrapper(wrapper, func)
```

In [ ]:
import functools

def prettier(func):
    @functools.wraps(func)
    def wrapper(*args, **kwargs):
        result = func(*args, **kwargs)
        print('.oOO Processing OOo.'.center(80))
        print(result)
        print('.oOO ~~~Done~~~ OOo.'.center(80))
        return result                            # Return func(*args, **kwargs)
    return wrapper

@prettier
def stuff(task, like_a=''):
    """Do stuff."""
    return f'Doing {task} like a {like_a}'.center(80)

## 3. Le module functools plus en détails

L'une des plus grandes forces de Python est qu'il fournit des outils permettant d'écrire du code facilement réutilisable. Nous avons déjà abordé cela avec les décorateurs. Le module standard `functools` fournit également des outils permettant de travailler avec des fonctions ou d'autre objets ***callables*** et d'adapter ou d'étendre leurs fonctionnalités pour pouvoir les réutiliser dans d'autres contextes.

Citons en particulier:

* `partial` permettant de créer des `partial functions`
* `singledispatch` permettant de créer des `generic functions`

Cette partie propose un tour d'horizon des possibilités offertes par `functools`.

### 3.1. Les ***partial functions***

Les ***partial functions*** sont des fonctions qui reproduisent le comportement d'une fonction de base en *"gelant"* certains de ses arguments. L'exemple suivant illustre ceci:

```python
from functools import partial

def repeat(char, n):
    print(f'{char*n:^80}')

stars = partial(repeat, char='*')
pipes = partial(repeat, char='|')
let_v = partial(repeat, char='v')
```

Les trois fonctions `stars`, `pipes` et `let_v` créées grâce à `partial` sont ainsi des spécialisation de `repeat`.

<div class="alert alert-block alert-info">
Implémentez ces <b><i>partial functions</i></b> et exécutez les tests suivant:
</div>

```python
stars(n=20)
pipes(n=10)
let_v(n=5)
```

Ces ***partial functions*** peuvent être utilisées comme des fonctions totalement indépendantes. Elles gardent cependant toujours la trace des fonctions ayant servi à leur création :
```python
>> stars.func
<function __main__.repeat(char, n)>
>> stars.keywords
{'char': '*'}
```

**Note:** *Ce concept de ***partial function*** s'étend également aux méthodes depuis Python 3.4. Il s'agit alors d'utiliser ***partialmethod*** aux lieu de ***partial***.*

### 3.2. Les ***Generic functions***

Une ***generic function*** est une fonction proposant dans le même ***scope*** différentes implémentations selon le type d'arguments. Ce type d'implémentation est possible grâce au décorateur `@singledispatch` fournit par le module `functools` depuis Python 3.4.

Une ***generic function*** est composée de plusieurs fonctions implémentant la même opération pour différents types. Un algorithme de répartition (***dispatch***) permet alors de déterminer quelle implémentation utiliser selon le type des arguments. En utilisant le décorateur `@singledispatch`, la répartition est choisie à partir du type d'un **unique** argument, d'où l'appellation ***single dispatch***.

Pour créer une ***generic function***:

* Décorer une fonction de base avec `@singledispatch`.
* Implémenter des fonctions alternatives en les décorant avec `@function_name.register(type)` où `function_name` est le nom de la fonction de base et `type` est le type du premier argument de cette fonction. Il est possible d'empiler les décorateurs.
* Le nom des implémentations alternatives doit être `_` si vous ne souhaitez qu'une seule fonction générique. Il est néanmoins possible de donner un nom aux implémentations alternatives. Dans ce cas, vous aurez la possibilité de les appeler directement.

>**Note 1:** *Si vous utilisez les **type annotations**, il n'est pas nécessaire de préciser le type à `register`:*
>```python
@display.register
def _(obj:list):
    strings = [str(i) for i in obj]
    print(f"List with elements {', '.join(strings)}")
```
**Note 2:** *`register()` peut être utilisé sous sa forme fonctionnelle afin d'être appliqué aux fonctions `lambda` par exemple:*
>```python
display.register(tuple, lambda obj: print('tuple:', obj))
```
**Note 3:** *Ce concept de ***generic function*** s'étend également aux méthodes depuis Python 3.8. Il s'agit alors d'utiliser ***singledispatchmethod*** aux lieu de ***singledispatch***.*


Par exemple:

In [ ]:
from functools import singledispatch
  
@singledispatch
def display(obj):
    raise NotImplementedError('Unsupported type')
 
@display.register(int)
@display.register(float)
def _(obj):
    print(f'Numerical object with value {obj}')

@display.register(list)
def _(obj):
    strings = [str(i) for i in obj]
    print(f"List with elements {', '.join(strings)}")

<div class="alert alert-block alert-info">
Exécutez les tests suivant pour comprendre le fonctionnement de <code>singledispatch</code>:
</div>

```python
display(1)
display(2.1)
display([1, 2])
display((1, 2))
```

### 3.3. La fonction `reduce`

La fonction `reduce` du module `functools` est souvent étudier en parallèle des fonctions `map` et `filter` car elle suit la même logique.

* `map` applique une fonction à tous les éléments d'une séquence. Il retourne un itérateur.
* `filter` crée un itérateur contenant tous les éléments d'une séquence pour lesquels la fonction a retourné `True`.
* `reduce` applique une fonction à deux arguments cumulativement sur tous les éléments d'une séquence.

Par exemple:
```python
>> list(map((lambda x: x**2), [1, 2, 3, 4]))
[1, 4, 9, 16]
>> list(filter((lambda x: x>2), [1, 2, 3, 4]))
[3, 4]
>> functools.reduce((lambda x, y: x*y), [1, 2, 3, 4])
24
```

Ce dernier exemple revient à:
```python
product = 1
for i in [1, 2, 3, 4]:
    product = product * i
```

Le fonctionnement de `reduce` est le suivant:

* la fonction est appliquée aux deux premiers éléments de la séquence,
* puis la fonction est appliquée au résultat précédent et au troisième élément, 
* puis cette méthode est appliquée aux éléments suivants,
* enfin, le résultat final est retourné.


>**Note:** *La fonction `reduce` de `functools` est similaire à la fonction `accumulate` de `itertools` aux exceptions suivantes près:*
>
>* `reduce` stocke les résultats intermédiaire et retourne uniquement le résultat final. 
* `accumulate` retourne une liste contenant les résultats intermédiaires. Le dernier élément de la liste est le résultat final.
* `reduce(function, sequence)` vs. `accumulate(sequence, function)`
* `accumulate` semble plus rapide:
>
>    * `%timeit functools.reduce((lambda x, y: x*y), [1, 2, 3, 4])`     => 553ns
>    * `%timeit itertools.accumulate([1, 2, 3, 4], (lambda x, y: x*y))` => 334ns


### 3.4. Automatisation des comparaisons

Le module `functools` fournit aussi un outil pour automatiser la création de fonctions de comparaison. Il s'agit du décorateur `@total_ordering`. Deux conditions doivent être satisfaites pour que l'automatisation se produise:

* Au moins une opération de comparaison doit être définie parmi `__le__`, `__lt__`, `__gt__` or `__ge__`.
* La méthode `__eq__` est requise.

Par exemple:

In [ ]:
import functools

@functools.total_ordering
class Int:
    def __init__(self, value):
        self.value = value
    def __eq__(self, other):
        return self.value == other.value
    def __gt__(self, other):
        return self.value > other.value

Toutes les opérations de comparaison sont alors disponibles pour les instances de `Int`:
```python
>> Int(1) <= Int(2)
True
```

<div class="alert alert-block alert-info">
Testez les autres opérations de comparaison.</div>

### 3.5. Mise en cache

Le module `functools` fournit également deux décorateurs utilisés pour optimiser des parties de code:

* `cached_property` (Python 3.8): Transforme une méthode de classe en `property` (cf. notebook correspondant dans la partie ***Classes & OOP***) dont la valeur n'est calculée qu'une fois et mise en cache pendant toute la durée de vie de l'instance. Ce décorateur est utilisé pour les ***properties*** dont le calcul est couteux.

* `lru_cache(maxsize)` (Python 3.2):  Enveloppe une fonction avec une mémorisation appelable qui permet d'enregistrer jusqu'au `maxsize` appels les plus récents. Ce décorateur permet de gagner du temps lorsqu'une fonction coûteuse ou liée à des E/S est appelée périodiquement avec les mêmes arguments.

## Bibliographie

* [Python.org - functools](https://docs.python.org/3.7/library/functools.html)
* [Journaldev.com - functools](https://www.journaldev.com/17550/python-functools)